In [1]:
from astropy.table import Table
from astropy import log
log.setLevel('WARNING')

import sys

### Catherine: interroger 2mass a partir d'une liste de positions
(par exemple une liste provenant d'un fichier)

In [2]:
def mem_list_position():
    listpos = []
    with open("list.txt","r") as fd:
        for line in fd:
            listpos.append(line.strip())
    return listpos

In [5]:
for pos in mem_list_position():
    print("!position {}".format(pos))
    
    url = "http://vizier.u-strasbg.fr/viz-bin/votable?-source=II/246/out&-c.rs=30&-c={}".format(pos)
    try:
        table = Table.read(url) 
    except Exception as e:
        sys.stderr.write(str(e)+"\n")  
        continue
        
    for rec in table["_2MASS"]:
        print ("o 2MASS {}".format(rec))
    

!position M1
o 2MASS 05343138+2201050
o 2MASS 05343146+2200567
o 2MASS 05343124+2201020
o 2MASS 05343185+2201081
o 2MASS 05343187+2201161
o 2MASS 05343188+2200460
o 2MASS 05343113+2201005
o 2MASS 05343029+2200528
o 2MASS 05343040+2200472
o 2MASS 05343104+2200567
o 2MASS 05343097+2201048
o 2MASS 05343194+2200521
o 2MASS 05343094+2200535
o 2MASS 05343296+2200416
o 2MASS 05343288+2200382
o 2MASS 05343342+2200584
o 2MASS 05343210+2200413
o 2MASS 05343217+2200560
o 2MASS 05343234+2201134
o 2MASS 05343232+2200491
!position 0+0


!position NGC234


No table found


o 2MASS 00433238+1420333


### generer les commandes gsc4sim 

In [6]:
from string import Template

template_2mass_string = '''
o 2MASS ${name}
a i 2MASS ${name}
!c c ${ra} ${dec} (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J ${jmag} [${e_jmag}] C 2003yCat.2246....0C
'''

template_2mass = Template(template_2mass_string)

In [7]:
def print_gsc4sim_2mass_out(table):
    for record in table:
        data = {'name': record["_2MASS"],
                'ra': record["RAJ2000"],
                'dec': record["DEJ2000"],
                'jmag': record["Jmag"],
                'e_jmag': record["e_Jmag"]}
        print (template_2mass.substitute(data))

In [12]:
import numpy

for pos in mem_list_position():
    print("!position {}".format(pos))
    url = "http://vizier.u-strasbg.fr/viz-bin/votable?-source=II/246/out&-c.rs=30&-c={}".format(pos)
    try:
        table = Table.read(url) 
    except Exception as e:
        sys.stderr.write(str(e)+"\n")  
        continue
    
    
    ind = numpy.where(table["Jmag"]<15)
    print_gsc4sim_2mass_out(table[ind])

!position M1

o 2MASS 05343138+2201050
a i 2MASS 05343138+2201050
!c c 83.630788 22.018076 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 14.068 [--] C 2003yCat.2246....0C


o 2MASS 05343185+2201081
a i 2MASS 05343185+2201081
!c c 83.632709 22.018929 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 14.62 [--] C 2003yCat.2246....0C


o 2MASS 05343113+2201005
a i 2MASS 05343113+2201005
!c c 83.629721 22.016808 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 13.951 [--] C 2003yCat.2246....0C


o 2MASS 05343029+2200528
a i 2MASS 05343029+2200528
!c c 83.626215 22.014688 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 14.696 [--] C 2003yCat.2246....0C


o 2MASS 05343040+2200472
a i 2MASS 05343040+2200472
!c c 83.626697 22.013136 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 14.59 [--] C 2003yCat.2246....0C


o 2MASS 05343194+2200521
a i 2MASS 05343194+2200521
!c c 83.633107 22.014486 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 14.576 [0.044] C 2003yCat.2246....0C


o 2MASS 05343296+2200416
a i 2M

!position NGC234


No table found



o 2MASS 00433238+1420333
a i 2MASS 00433238+1420333
!c c 10.884946 14.342605 (NIR) B [70 70 90] 2003yCat.2246....0C
!c m J 13.88 [0.105] C 2003yCat.2246....0C



### alternative: utiliser de pack cdsclient 
- telecharger le package python: http://cds.u-strasbg.fr/resources/doku.php?id=cdsclient
- tar -xzvf python-cdsclient_1.1.xxx.tar.gz
- cp python-cdsclient/vizquery.py . ; cp python-cdsclient/finf_2mass.py .

In [13]:
import find_2mass

In [14]:
def query_2mass_2(position, radius=10):
    process = find_2mass.QueryCatVizieR()
    process.position = position
    process.radius = radius
    process.query_cat(limit=10)
    
    try:
        return process.get()
    except:
        return None

In [15]:
process = find_2mass.QueryCatVizieR()

for pos in mem_list_position():
    print("!position {}".format(pos))
    
    process.position = pos
    process.radius = 30
    process.query_cat(limit=10)
    
    try:
        table = process.get()
    except Exception as e:
        sys.stderr.write(str(e)+"\n")
        continue
        
    print (table)

!position M1
  col1    col2   col3 col4  col5  col6 ... col10 col11 col12 col13 col14 col15
------- ------- ----- ---- ------ ---- ... ----- ----- ----- ----- ----- -----
RAJ2000 DEJ2000 2MASS Jmag e_Jmag Hmag ...  Qflg  Rflg  Bflg  Cflg  Xflg  Aflg
deg	deg   mag	m g	mag  mag ag	mag   -- ...    --    --    --    --    --    --
------- --	---- ----- ---- ------ ---- ...  --	-  ----  ----  -	--   ---  --	-
083.630 88	+22. 18076 0534 138+22 1050 ...    85  .274  12.7     6    --  DU	0
083.631 11	+22. 15774 0534 146+22 0567 ...    13  .190  14.2  2	 0   127  CB	2
083.630 95	+22. 17235 0534 124+22 1020 ...    79    --  12.5     4    --  UU	2
083.632 09	+22. 18929 0534 185+22 1081 ...    06    --  14.4  8	 0   162  UC	0
083.632 03	+22. 21156 0534 187+22 1161 ...    80  .153  13.9  0	 0   124  BB	2
083.632 57	+22. 12794 0534 188+22 0460 ...    79  .145  16.5  1	 0   602  BD	2
083.629 21	+22. 16808 0534 113+22 1005 ...    63    --  14.0  3	 0   168  UC	0
083.626 15	+22. 14688 0534 029+22 0528 

No data lines found so cannot autogenerate column names


  col1    col2   col3 col4  col5  col6 ... col10 col11 col12 col13 col14 col15
------- ------- ----- ---- ------ ---- ... ----- ----- ----- ----- ----- -----
RAJ2000 DEJ2000 2MASS Jmag e_Jmag Hmag ...  Qflg  Rflg  Bflg  Cflg  Xflg  Aflg
deg	deg   mag	m g	mag  mag ag	mag   -- ...    --    --    --    --    --    --
------- --	---- ----- ---- ------ ---- ...  --	-  ----  ----  -	--   ---  --	-
010.884 46	+14. 42605 0043 238+14 0333 ...    36  .171  12.8  8	 0   092  EE	2
